In [1]:
import json
import tensorflow as tf
import numpy as np
from __future__ import print_function
from keras.models import Model
from keras.layers import Input, LSTM, Dense

batch_size = 64  
epochs = 100  
latent_dim = 256  
num_samples = 5000
num_test = 100

data_path = 'translation2019zh_train.json'

train_texts = []
test_data = []
input_texts = []
target_texts = []

input_file = open(data_path, encoding = 'utf8')
for i,line in enumerate(input_file.readlines(),1):
    if i > num_samples + num_samples:
        break
    elif i > num_samples:
        test_data.append(json.loads(line))
    else:
        train_texts.append(json.loads(line))
input_file.close()

input_characters = set()
target_characters = set()

for train_text in train_texts:
    input_text = train_text['english']
    target_text = '\t' + train_text['chinese'] + '\n'
    input_texts.append(input_text)
    target_texts.append(target_text)
    for char in input_text:
        if char not in input_characters:
            input_characters.add(char)
    for char in target_text:
        if char not in target_characters:
            target_characters.add(char)

input_characters = sorted(list(input_characters))
target_characters = sorted(list(target_characters))
num_encoder_tokens = len(input_characters)
num_decoder_tokens = len(target_characters)

max_encoder_seq_length = max([len(txt) for txt in input_texts])
max_decoder_seq_length = max([len(txt) for txt in target_texts])

print('Number of samples:', len(input_texts))
print('Number of unique input tokens:', num_encoder_tokens)
print('Number of unique output tokens:', num_decoder_tokens)
print('Max sequence length for inputs:', max_encoder_seq_length)
print('Max sequence length for outputs:', max_decoder_seq_length)

input_token_index = dict([(char, i) for i, char in enumerate(input_characters)])
target_token_index = dict([(char, i) for i, char in enumerate(target_characters)])

encoder_input_data = np.zeros((len(input_texts), max_encoder_seq_length, num_encoder_tokens),dtype='float32')
decoder_input_data = np.zeros((len(input_texts), max_decoder_seq_length, num_decoder_tokens),dtype='float32')
decoder_target_data = np.zeros((len(input_texts), max_decoder_seq_length, num_decoder_tokens),dtype='float32')


for i, (input_text, target_text) in enumerate(zip(input_texts, target_texts)):
    for t, char in enumerate(input_text):
        encoder_input_data[i, t, input_token_index[char]] = 1.
    for t, char in enumerate(target_text):
        decoder_input_data[i, t, target_token_index[char]] = 1.
        if t > 0:
            decoder_target_data[i, t - 1, target_token_index[char]] = 1.

encoder_inputs = Input(shape=(None, num_encoder_tokens))
encoder = LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)
encoder_states = [state_h, state_c]
decoder_inputs = Input(shape=(None, num_decoder_tokens))
decoder_lstm = LSTM(latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_inputs,initial_state=encoder_states)
decoder_dense = Dense(num_decoder_tokens, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
model.compile(optimizer='rmsprop', loss='categorical_crossentropy')
model.fit([encoder_input_data, decoder_input_data], decoder_target_data, batch_size=batch_size, epochs=epochs, validation_split=0.2)
model.save('s2s.h5')

Number of samples: 5000
Number of unique input tokens: 319
Number of unique output tokens: 3528
Max sequence length for inputs: 282
Max sequence length for outputs: 150
Epoch 1/100
63/63 [==============================] - 274s 4s/step - loss: 1.6824 - val_loss: 1.6831
Epoch 2/100
63/63 [==============================] - 221s 4s/step - loss: 1.6460 - val_loss: 1.6769
Epoch 3/100
63/63 [==============================] - 215s 3s/step - loss: 1.6414 - val_loss: 1.6756
Epoch 4/100
63/63 [==============================] - 222s 4s/step - loss: 1.6376 - val_loss: 1.6739
Epoch 5/100
63/63 [==============================] - 220s 4s/step - loss: 1.6363 - val_loss: 1.6719
Epoch 6/100
63/63 [==============================] - 225s 4s/step - loss: 1.6353 - val_loss: 1.6709
Epoch 7/100
63/63 [==============================] - 219s 3s/step - loss: 1.6347 - val_loss: 1.6692
Epoch 8/100
63/63 [==============================] - 226s 4s/step - loss: 1.6342 - val_loss: 1.6718
Epoch 9/100
63/63 [============

63/63 [==============================] - 226s 4s/step - loss: 1.6167 - val_loss: 1.6576
Epoch 81/100
63/63 [==============================] - 232s 4s/step - loss: 1.6169 - val_loss: 1.6581
Epoch 82/100
63/63 [==============================] - 281s 4s/step - loss: 1.6160 - val_loss: 1.6596
Epoch 83/100
63/63 [==============================] - 225s 4s/step - loss: 1.6153 - val_loss: 1.6669
Epoch 84/100
63/63 [==============================] - 226s 4s/step - loss: 1.6152 - val_loss: 1.6642
Epoch 85/100
63/63 [==============================] - 230s 4s/step - loss: 1.6139 - val_loss: 1.6584
Epoch 86/100
63/63 [==============================] - 231s 4s/step - loss: 1.6138 - val_loss: 1.6604
Epoch 87/100
63/63 [==============================] - 236s 4s/step - loss: 1.6129 - val_loss: 1.6572
Epoch 88/100
63/63 [==============================] - 232s 4s/step - loss: 1.6134 - val_loss: 1.6594
Epoch 89/100
63/63 [==============================] - 225s 4s/step - loss: 1.6122 - val_loss: 1.6581
Epo

In [15]:
encoder_model = Model(encoder_inputs, encoder_states)
decoder_state_input_h = Input(shape=(latent_dim,))
decoder_state_input_c = Input(shape=(latent_dim,))
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]
decoder_outputs, state_h, state_c = decoder_lstm(decoder_inputs, initial_state=decoder_states_inputs)
decoder_states = [state_h, state_c]
decoder_outputs = decoder_dense(decoder_outputs)
decoder_model = Model([decoder_inputs] + decoder_states_inputs,[decoder_outputs] + decoder_states)
reverse_input_char_index = dict((i, char) for char, i in input_token_index.items())
reverse_target_char_index = dict((i, char) for char, i in target_token_index.items())
def decode_sequence(input_seq):
    states_value = encoder_model.predict(input_seq)

    target_seq = np.zeros((1, 1, num_decoder_tokens))
    target_seq[0, 0, target_token_index['\t']] = 1.

    stop_condition = False
    decoded_sentence = ''
    while not stop_condition:
        output_tokens, h, c = decoder_model.predict([target_seq] + states_value)

        sampled_token_index = np.argmax(output_tokens[0, -1, :])
        sampled_char = reverse_target_char_index[sampled_token_index]
        decoded_sentence += sampled_char

        if (sampled_char == '\n' or len(decoded_sentence) > max_decoder_seq_length):
            stop_condition = True

        target_seq = np.zeros((1, 1, num_decoder_tokens))
        target_seq[0, 0, sampled_token_index] = 1.

        states_value = [h, c]

    return decoded_sentence

test_texts = []
test_characters = set()
for text in test_data:
    test_texts.append(text['english'])
    for char in text['english']:
        if char not in test_characters:
            test_characters.add(char)
            
test_characters = sorted(list(test_characters))
num_test = len(test_characters)
test_index = dict([(char, i) for i, char in enumerate(test_characters)])
test_input_data = np.zeros((len(input_texts), max_encoder_seq_length, num_encoder_tokens), dtype='float32')

In [22]:
for seq_index in range(len(test_data)):
    input_seq = test_input_data[seq_index: seq_index + 1]
    decoded_sentence = decode_sequence(input_seq)
    print(seq_index + 1, '.')
    print('English:', test_data[seq_index])
    try:
        print('Chinese:', decoded_sentence)
    except:
        print('Chinese:', decoded_sentence.encode('ascii', 'replace'))

1 .
English: {'english': 'But in before this long reaches for several months to rescue in the city or not argument, the supervising and managing level has not said a word.', 'chinese': '而在此前长达数月的救市与否的争论中，监管层未发一言。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，
2 .
English: {'english': 'With their help, all the apples were picked and put back on the cart.', 'chinese': '侥幸的是，苏和汽车司机都没受伤。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的
3 .
English: {'english': "Crohn's disease (CD) is a chronic transmural inflammatory disease that may involve any part of the alimentary tract from mouth to anus.", 'chinese': '克隆氏病症是一种可侵犯消化道任何一部份的慢性全肠壁层侵犯的发炎疾病。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，

24 .
English: {'english': 'On January 23, thousands of Bangladeshi Muslims boarded overcrowded trains as they tried to return home after attending the three-day World Islamic Congregation in Dhaka, Bangladesh.', 'chinese': '1月23日，在孟加拉国首都达卡，数千名穆斯林教徒参加完为期三天的世界穆斯林代表大会后，挤火车回家。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
25 .
English: {'english': 'Handlers that do not process, repack or re-label organic products do not need to be certified.', 'chinese': '不对有机产品进行加工、不换包装或不换标签的贸易商不必认证。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
26 .
English: {'english': 'Several studies were commissioned, and a variety of panels heard expert witnesses and took testimony about the need for reform.', 'chinese': '有关方面围绕改革的需要展开了数项研究，举行了多种专题会议，听取专家意见和举行听证。'}
Chinese: 我们们，，，，，，，，，

47 .
English: {'english': 'The results indicated that the ICA in three algorithms JADE, MSNR, GOSA can be extracted to structure mode, which had a good consistency with the modal parameters from the OMA.', 'chinese': '研究结果表明ICA中的JADE、MSNR、GOSA三种算法均可提取试验模型的结构模态参数，它与OMA提取的模态参数具有良好的一致性。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
48 .
English: {'english': 'Would you like to go bicycling with me in the mountains?', 'chinese': '要不要和我—起去山里骑自行车？'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
49 .
English: {'english': "Men's ability to turn a sniffle into flu and a headache into a migraine has long been a source of irritation to wives and girlfriends.", 'chinese': '男性将流鼻涕转变成流感，将轻微头痛转变成偏头痛的“能力”，长期以来一直是激怒他们妻子和女朋友的一个根源。 （因为普遍认为女性在流感面前更脆弱。）'}
Chinese: 我们们，，，，，，，，，，，，

70 .
English: {'english': 'The stabilizing effect of hot-electron and line-tying on the low-frequency plasma interchange mode is analysed.', 'chinese': '分析了热电子与线捆对低频等离子体交换模的稳定作用。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
71 .
English: {'english': 'So I think there are very many similarities between what’s happening in Europe and what’s happening in the Arab world.', 'chinese': '因此，我认为，欧洲所发生的事情和阿拉伯世界所发生的动荡之间有很多相似之处。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
72 .
English: {'english': 'When he fell from the cliff, he beat his brains out.', 'chinese': '他从悬崖上跌了下去， 头破血流而死。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
73 .
English: {'engli

92 .
English: {'english': 'Black hole of algorithms, and the dichotomy, I wrote some satay to know that they feel can also.', 'chinese': '黑洞的算法，和二分法，我写的，嗲给知道一些，自己感觉还可以。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
93 .
English: {'english': 'if the time period of paying premiums is not less than ten years, the maximum period of receiving unemployment insurance compensation is 24 months;', 'chinese': '累计缴费时间10年以上的，领取失业保险金的期限最长为24个月。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
94 .
English: {'english': 'Inverse triangle: a similar heart-shaped, the amount of large, small jaw, are one of the ideal type face, all the collars are suitable.', 'chinese': '逆三角形：类似心形，上额宽大，下颚狭小，是属于理想型脸型之一，所有的领子都适合。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，

...

4901 .
English: {'english': 'The companys business scope: production and sale of coke and by - products, pig iron , cement and related products, electricity, carbon products;', 'chinese': '公司的经营范围：生产、销售焦炭及副产品、生铁、水泥及制品、电力、炭素制品；'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4902 .
English: {'english': "Alessandro Del Piero seems to have recovered from the injury which kept him out from Tuesday's match against Crotone.", 'chinese': '德尔。皮耶罗因为伤病缺席了对克罗托内的比赛，但现在看来他的伤似乎没有大碍了。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4903 .
English: {'english': 'The onset of the economic crisis two years ago threatened demand for subscriptions, throwing into stark relief the risks of relying on a costly, one-size-fits-all product.', 'chinese': '发端于两年前的经济危机对订阅服务的需求产生了威胁，凸显出依赖昂贵

4926 .
English: {'english': 'We do it outside in the yard in summer and inside during the winter. My kids are already experts.', 'chinese': '夏天时我们在院子里跳绳,而冬天在屋内.我的孩子们已经很在行了.我还在学,或者说是再学.'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4927 .
English: {'english': 'But this feeling was an illusion that is rapidly dissipating.', 'chinese': '然而，这种感觉也只不过是镜花水月，很快就要消弭殆尽。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4928 .
English: {'english': 'He has already clearly stated his position on this issue before the debate in public.', 'chinese': '他在这个问题公开进行辨论之前就已表明了自己的立场。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4929 .
English: {'english': "But then t

4949 .
English: {'english': 'The starting material 2,4-dinitroaniline was partially reduced in a mixed solvent to afford 4-nitro-1,2-phenylenediamine.', 'chinese': '用2，4-二硝基苯胺为原料，在混合溶剂中进行部分还原，得到对硝基邻苯二胺。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4950 .
English: {'english': "This was the first animated work based on Tezuka Osamu's Manga that was planned following his death.", 'chinese': '这是第一个动画工作的基础上手冢修的漫画是计划后死亡。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4951 .
English: {'english': 'As for the "Li-jen", mainly from the wisdom of speaking, that the wisdom of those who favor the completion of Rende.', 'chinese': '至于“利仁”，主要是从智慧上说的，即智慧的人有利于仁德的完成。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，

4973 .
English: {'english': 'Breathe out through pursed lips as if you were whistling.', 'chinese': '从闭合嘴唇中呼气，就好像在吹口哨。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4974 .
English: {'english': 'The art of Diabolo in Beijing is getting development quickly. So does it in other cities, such as Henan, Shanghai, Wuhan, inner-Mongolia.', 'chinese': '北京空竹发展特别快，外地也是，像是大城市，河南，上海，武汉，…'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4975 .
English: {'english': 'The sightseer on the tower watches you.', 'chinese': '看风景的人在楼上看你。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4976 .
English: {'english': 'Return the home, ravel the book, amazed discovery " hil

4997 .
English: {'english': 'Residents should also require the management companies to record the information of strangers accessing the buildings and install close circuit televisions.', 'chinese': '住户亦应要求所居住大厦的管理公司记录出入大厦陌生人的资料，并且装置摄录机，除收阻吓作用外亦可在需要时协助破案。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4998 .
English: {'english': 'VOICE: So it sounds as if anabolic steroids can be very destructive.', 'chinese': '所以，听起来合成代谢类固醇的破坏性会很大。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，，的，，的，，的，，的，，的，的，的的的的的的，的的，的，的的，的的，的的，的，的的
4999 .
English: {'english': 'It is a form of teaching experiment and research, including group preparing lessons, teachers\' drills, "2+2" teaching guidance and teaching improvement.', 'chinese': '以教研组集体备课，教师演练，“2+2”教学指导原则，改良再行动为课堂教学实验与研究的一种活动形式。'}
Chinese: 我们们，，，，，，，，，，，，，，，，，，，，，，，

In [27]:
print(test_data)

[{'english': 'But in before this long reaches for several months to rescue in the city or not argument, the supervising and managing level has not said a word.', 'chinese': '而在此前长达数月的救市与否的争论中，监管层未发一言。'}, {'english': 'With their help, all the apples were picked and put back on the cart.', 'chinese': '侥幸的是，苏和汽车司机都没受伤。'}, {'english': "Crohn's disease (CD) is a chronic transmural inflammatory disease that may involve any part of the alimentary tract from mouth to anus.", 'chinese': '克隆氏病症是一种可侵犯消化道任何一部份的慢性全肠壁层侵犯的发炎疾病。'}, {'english': 'Be thankful that when you go to buy a pale, poultrylike entity, the grocery clerk will accept your credit card in good faith and even return it with a heroic garble of your last name.', 'chinese': '你应该感谢，当你买回一堆毫无生气的禽肉时，杂货店收银员诚心诚意地为你刷卡，即使在归还信用卡时，张冠李戴地称呼你。'}, {'english': 'You can achieve this goal by applying SOA, BPM, and EA together in a synergistic fashion.', 'chinese': '通过协作方式一起应用 SOA、BPM 和 EA 可以实现此目标。'}, {'english': 'This paper mainly introduced the gas spre